In [1]:
import requests
import pandas as pd
import numpy as np
import matplotlib.pyplot as plt
from sklearn.linear_model import LinearRegression as LR
import tarfile
import io

import os

In [18]:
def get_api(rpt: str, elem: str, grid: str, time_rsltn: str, st_year: str, ed_year: str, fmat: str, auth_key: str):
    url = f'https://apihub-org.kma.go.kr/api/typ01/url/ssp_skorea_file_down.php?rpt={rpt}&model=5ENSMN&elem={elem}&grid={grid}&time_rsltn={time_rsltn}&st_year={st_year}&ed_year={ed_year}&frmat={fmat}&authKey={auth_key}'
    response = requests.get(url)
    file_like = io.BytesIO(response.content)
    with tarfile.open(fileobj=file_like, mode='r:gz') as tar:
        tar.list()

        # txt 파일 찾기
        members = tar.getmembers()
        for member in members:
            if member.isfile() and member.name.endswith('.txt'):
                # txt 파일 읽기
                file = tar.extractfile(member)
                if file is not None:
                    # 데이터 프레임으로 변경
                    df = pd.read_csv(file)
                    if not os.path.isdir(f'./SSP585_ASOS/{member.name[:-9]}'):
                        os.makedirs(f'./SSP585_ASOS/{member.name[:-9]}')
                    df.to_csv(f'./SSP585_ASOS/{member.name[:-9]}/{member.name[:-4]}.csv', index=False, encoding='utf-8 sig')

In [19]:
elems = ['TA', 'TAMAX', 'TAMIN', 'RN', 'RHM', 'WS', 'SI']
# , 'SST', 'SLR', 'SALNT', 'SICONCA', # 기후요소 
#          'TR25', 'HW33', 'SU25', 'GSL', 'DTR', 'TX90P', 'WSDI', 'WSDIx', 'TN90P', 'TXx', 'TNx', # 극한 기후 지수
#          'FD0', 'ID0', 'CWm12', 'TX10P', 'CSDI', 'CSDIx', 'TN10P', 'TXn', 'TNn', 'SDII', 'RAIN80', # 극한 기후 지수
#          'CDD', 'RX1DAY', 'RX5DAY', 'RD95P', 'RD99P'] # 극한 기후 지수
auth_key = 'F-CGdETAS-WghnREwPvlog'
for elem in elems:
    try:
        get_api('SSP585', elem, 'asos95','daily', '2021', '2100', 'asc', auth_key)
    except:
        print(elem)
        continue

TA
TAMAX
TAMIN
RN
RHM
WS
SI


In [20]:
data_names = ['RN', 'RHM', 'SI', 'TA', 'TAMAX', 'TAMIN', 'WS']
# 80년 데이터 합치기
for name in data_names:
    PATH = f'SSP585_ASOS/AR6_SSP585_5ENSMN_skorea_{name}_asos95_daily'
    dirlist = os.listdir(f'./{PATH}') # 디렉토리 가져오기
    main_df = pd.DataFrame() # 빈 데이터 프레임

    # 데이터 프레임 합치기
    for path in dirlist:
        df = pd.read_csv(f'./{PATH}/{path}')
        main_df = pd.concat([main_df,df],axis=0)
        
    # 지점명 가져오기
    area_name = list(main_df.loc[0].reset_index(drop=True).loc[0])
    area_name.pop(0)

    # 필요없는 데이터 삭제
    main_df.drop(0,axis=0,inplace=True)

    # 날짜로 인덱스 바꾸기
    main_df = main_df.set_index('년-월-일')

    # 저장
    if not os.path.isdir('./SSP585_ASOS/concat_data'):
        os.makedirs('./SSP585_ASOS/concat_data')
    main_df.to_csv(f'./SSP585_ASOS/concat_data/{name}.csv',encoding='utf-8 sig')

In [21]:
import time
# 합친데이터 불러와서 dict에 저장하기
dfs = {}
for name in data_names:
    dfs[name] = pd.read_csv(f'./SSP585_ASOS/concat_data/{name}.csv', index_col='년-월-일')

# 컬럼명 가져오기
cols = dfs['RN'].columns

# 지점 코드랑 지점명 dict로 저장하기
ids = {} # key : 지점코드 value : 지점명
for i in range(len(cols)):
    ids[cols[i]] = area_name[i]

# 지점명으로 데이터 정리하기
for id in ids.keys():
    ddf = pd.DataFrame(columns=dfs.keys())
    for col in ddf.columns:
        ddf[col] = dfs[col][id]

    if not os.path.isdir('./SSP585_ASOS/DATA'):
        os.makedirs('./SSP585_ASOS/DATA')
    ddf.to_csv(f'./SSP585_ASOS/DATA/{ids[id]}.csv', encoding='utf-8 sig')

In [2]:
def qcEtccdi(df,daterange,nan_set):
    start_ymd=daterange[0]
    end_ymd=daterange[1]
    df['YMD']=pd.DatetimeIndex(df['YR'].astype(str)+'-'+df['MM'].astype(str)+'-'+df['DD'].astype(str))
    if start_ymd > end_ymd:
        print('startYMD should be earlier than endYMD')
        raise SystemExit(0)
    df=df[df['YMD'].between(pd.to_datetime(start_ymd), pd.to_datetime(end_ymd+'-12-31'))]
    if df.isnull().values.any():
        if nan_set==1:
            df.dropna(inplace=True)
            print('nan values have been dropped')
        elif nan_set==0:
            df.fillna(method='bfill', inplace=True)
            print('nan values have been replaced by backward fill and forward fill')
        elif nan_set==-1:
            print('There are nan values in the data, please check the data')
    df.index=pd.to_datetime(df['YMD'])
    df['JULYAN']=df.index.dayofyear
    return df

def get_coef(factor: pd.Series) -> tuple:

    ind=factor.groupby(factor.index.get_level_values(0)).max().index
    val=factor.groupby(factor.index.get_level_values(0)).max().values

    lr_F1=LR()
    lr_F2=LR()
    lr_F3=LR()

    lr_F1.fit(ind.values.reshape(-1,1)[:30], val[:30])
    lr_F2.fit(ind.values.reshape(-1,1)[30:60], val[30:60])
    lr_F3.fit(ind.values.reshape(-1,1)[60:], val[60:])

    return map(float,[lr_F1.coef_[0],lr_F2.coef_[0],lr_F3.coef_[0]])

In [3]:
directory = './SSP585_ASOS/DATA'
files = os.listdir(directory)
city_list = [file.replace('.csv', '') for file in files if file.endswith('.csv')] #  ['asda',]
city_list.sort()
df_coef_fin = pd.DataFrame()
for city in city_list:
    path = f'./SSP585_ASOS/DATA/{city}.csv'
    # columns = ['YR','MM','DD','RN','TMAX','TMIN']
    daterange=('2021', '2100')
    # nan values( if 1, then nan values will drop, if 0, then nan values will be replaced by backward fill or forward fill, if -1, program will stop)
    nan_set=1
    # RNN파라미터
    user_defined_precipitation_threshold=10

    df = pd.read_csv(path)
    df['년-월-일'] = pd.to_datetime(df['년-월-일'])

    # 데이터 프레임 datetime 변경
    df['YR'] = df['년-월-일'].dt.year
    df['MM'] = df['년-월-일'].dt.month
    df['DD'] = df['년-월-일'].dt.day
    df = df.drop(['년-월-일'],axis=1)
    df = df[['YR','MM','DD','RN','RHM','SI','TA','TAMAX','TAMIN','WS']]
    df_qc = qcEtccdi(df,daterange,nan_set)
    df = df_qc.copy()
    ## 극한 강우 지수 산출
    # var: TAMAX
    SU25=df.groupby(df['YMD'].dt.year)['TAMAX'].apply(lambda x: (x > 25).sum())
    ID0=df.groupby(df['YMD'].dt.year)['TAMAX'].apply(lambda x: (x < 0).sum())
    TXN=df.groupby([df['YR'],df['MM']])['TAMAX'].min()
    TXX=df.groupby([df['YR'],df['MM']])['TAMAX'].max()
    TX10p=df.groupby([df['YR'],df['MM']])['TAMAX'].quantile(0.1)
    TX90p=df.groupby([df['YR'],df['MM']])['TAMAX'].quantile(0.9)
    # WSDI

    # var: TAMIN
    FD0=df.groupby(df['YMD'].dt.year)['TAMIN'].apply(lambda x: (x < 0).sum())
    TR20=df.groupby(df['YMD'].dt.year)['TAMIN'].apply(lambda x: (x > 20).sum())
    TNN=df.groupby([df['YR'],df['MM']])['TAMIN'].min()
    TNX=df.groupby([df['YR'],df['MM']])['TAMIN'].max()
    TN10p=df.groupby([df['YR'],df['MM']])['TAMIN'].quantile(0.1)
    TN90p=df.groupby([df['YR'],df['MM']])['TAMIN'].quantile(0.9)
    # CSDI

    # TAMAX TAMIN
    DTR=df.groupby([df['YR'],df['MM']])['TAMAX'].mean()-df.groupby([df['YR'],df['MM']])['TAMIN'].mean()
    # GSL

    # var: PRCP
    CDD=df.groupby(df['YMD'].dt.year)['RN'].apply(lambda x: (x < 1).astype(int).groupby((x >= 1).astype(int).cumsum()).cumsum().max())
    CWD=df.groupby(df['YMD'].dt.year)['RN'].apply(lambda x: (x >= 1).astype(int).groupby((x < 1).astype(int).cumsum()).cumsum().max())
    PRCPTOT=df.groupby(df['YMD'].dt.year)['RN'].sum()
    RX1day=df.groupby([df['YR'],df['MM']])['RN'].max()
    RX5day=df.groupby([df['YR'], df['MM']])['RN'].rolling(5).sum()
    # MultiIndex를 가진 시리즈에서 YMD를 사용하여 인덱스를 일단위로 정렬
    RX5day.index = pd.to_datetime(RX5day.index.get_level_values('YMD'))

    # 연도별 RX5day 계산
    RX5day = RX5day.groupby(RX5day.index.year).max()

    
    R95P=df.groupby([df['YR'],df['MM']])['RN'].quantile(0.95)
    R99P=df.groupby([df['YR'],df['MM']])['RN'].quantile(0.99)
    SDII=df.groupby(df['YMD'].dt.year)['RN'].sum() / (df.groupby(df['YMD'].dt.year)['RN'].apply(lambda x: (x > 1).sum()))
    RNN=df.groupby(df['YMD'].dt.year)['RN'].apply(lambda x: (x < user_defined_precipitation_threshold).sum())
    R10=df.groupby(df['YMD'].dt.year)['RN'].apply(lambda x: (x > 10).sum())
    R20=df.groupby(df['YMD'].dt.year)['RN'].apply(lambda x: (x > 20).sum())
    R72=df.groupby(df['YMD'].dt.year)['RN'].apply(lambda x: (x > 72).sum())
    R100=df.groupby(df['YMD'].dt.year)['RN'].apply(lambda x: (x > 100).sum())

    ## 이미지 그리기
    # TXx, TNx, TNx, TNn 그리기
    plt.figure(figsize=(8,5))

    ind_TXX=TXX.groupby(TXX.index.get_level_values(0)).max().index
    val_TXX=TXX.groupby(TXX.index.get_level_values(0)).max().values

    plt.plot(ind_TXX,val_TXX,color = '#FE0000',label='TXx')

    ind_TNX=TNX.groupby(TNX.index.get_level_values(0)).max().index
    val_TNX=TNX.groupby(TNX.index.get_level_values(0)).max().values

    plt.plot(ind_TNX,val_TNX,color = '#EA7676', label='TNx')

    ind_TXN=TXN.groupby(TXN.index.get_level_values(0)).min().index
    val_TXN=TXN.groupby(TXN.index.get_level_values(0)).min().values

    plt.plot(ind_TXN,val_TXN,color = '#6FA2ED', label='TXn')

    ind_TNN=TNN.groupby(TNN.index.get_level_values(0)).min().index
    val_TNN=TNN.groupby(TNN.index.get_level_values(0)).min().values

    plt.plot(ind_TNN,val_TNN,color = '#1E00FE', label='TNn')
    
    # 그래프 정보 넣기
    plt.grid()
    plt.title('TXx,TXn,TNx,TNn')
    plt.xlabel('Year')
    plt.ylabel('Temp(℃)')
    plt.legend(loc='upper left', bbox_to_anchor=(1,1))
    if not os.path.isdir(f'./SSP585_ASOS/DATA/{city}'):
        os.makedirs(f'./SSP585_ASOS/DATA/{city}')

    # 이미지 저장
    plt.savefig(f'./SSP585_ASOS/DATA/{city}/TA.png', bbox_inches='tight')

    # 이미지 초기화
    plt.clf()

    # TX10, TX90 그리기
    ind_TX10p=TX10p.groupby(TX10p.index.get_level_values(0)).max().index
    val_TX10p=TX10p.groupby(TX10p.index.get_level_values(0)).max().values

    plt.plot(ind_TX10p,val_TX10p,color = 'r',label='TX10p')

    ind_TX90p=TX90p.groupby(TX90p.index.get_level_values(0)).max().index
    val_TX90p=TX90p.groupby(TX90p.index.get_level_values(0)).max().values

    plt.plot(ind_TX90p,val_TX90p,color = 'b',label='TX90p')

    # 두 그래프 사이 칠하기
    plt.fill_between(ind_TX90p,val_TX10p,val_TX90p, color='gray', alpha=0.3)
    plt.legend()
    plt.grid()
    plt.xlabel('year')
    plt.ylabel('Temp(℃)')
    plt.title('TX10,90P')

    # 이미지 저장
    plt.savefig(f'./SSP585_ASOS/DATA/{city}/TX10,90P.png', bbox_inches='tight')

    # 이미지 초기화
    plt.clf()

    # TN10, TN90 그리기
    ind_TN10p=TN10p.groupby(TN10p.index.get_level_values(0)).max().index
    val_TN10p=TN10p.groupby(TN10p.index.get_level_values(0)).max().values

    plt.plot(ind_TN10p,val_TN10p,color = 'r',label='TN10p')

    ind_TN90p=TN90p.groupby(TN90p.index.get_level_values(0)).max().index
    val_TN90p=TN90p.groupby(TN90p.index.get_level_values(0)).max().values

    plt.plot(ind_TN90p,val_TN90p,color = 'b',label='TN90p')

    # 두 그래프 사이 칠하기
    plt.fill_between(ind_TN90p,val_TN10p,val_TN90p, color='gray', alpha=0.3)
    plt.legend()
    plt.grid()
    plt.title('TN10,90P')
    plt.xlabel('year')
    plt.ylabel('Temp(℃)')

    # 이미지 저장
    plt.savefig(f'./SSP585_ASOS/DATA/{city}/TN10,90P.png', bbox_inches='tight')

    # 이미지 초기화
    plt.clf()

    # SU ID FD TR CDD CWD Rx1day R20 그리기
    mm = ['RX1day', 'RX5day', 'R95P', 'R99P', 'PRCPTOT', 'SDII']
    factors = {'SU': SU25, # day
            'ID': ID0, #
            'FD': FD0,
            'TR': TR20,
            'CDD': CDD,
            'CWD': CWD,
            'R10': R10,
            'R20': R20,  # day
            'R72': R72,
            'R100': R100,
            'RX1day': RX1day, # mm
            'RX5day': RX5day, # mm
            'R95P': R95P, # mm
            'R99P': R99P, # mm 
            'PRCPTOT': PRCPTOT, # mm
            'SDII': SDII,  # mm
            'DTR': DTR} # ℃
    for name,item in factors.items():
        
        ind=item.groupby(item.index.get_level_values(0)).max().index
        val=item.groupby(item.index.get_level_values(0)).max().values

        # 그래프 그리기
        plt.plot(ind,val,color = 'r',label=name)

        # 그래프 정보 넣기
        plt.title(name)
        plt.grid()
        plt.xlabel('year')
        if name in mm:
            plt.ylabel('mm')
        elif name == 'DTR':
            plt.ylabel('Temp(℃)')
        else:
            plt.ylabel('day')

        # 추세선 그리기
        lr_model_F1=LR()
        lr_model_F2=LR()
        lr_model_F3=LR()
        
        lr_model_F1.fit(ind.values.reshape(-1,1)[:30], val[:30])
        lr_model_F1.coef_
    
        lr_model_F2.fit(ind.values.reshape(-1,1)[30:60], val[30:60])
        lr_model_F2.coef_

        lr_model_F3.fit(ind.values.reshape(-1,1)[60:], val[60:])
        lr_model_F3.coef_

        plt.plot(ind[:30],lr_model_F1.predict(ind.values.reshape(-1,1)[:30]), color='b',lw=0.8,label='trend line')
        plt.plot(ind[30:60],lr_model_F2.predict(ind.values.reshape(-1,1)[30:60]), color='b',lw=0.8)
        plt.plot(ind[60:],lr_model_F3.predict(ind.values.reshape(-1,1)[60:]), color='b',lw=0.8)

        plt.text(ind[14], min(val) - 0.05, f"{lr_model_F1.coef_[0]:.4f}", ha='center', va='top', color='black')
        plt.text(ind[44], min(val) - 0.05, f"{lr_model_F2.coef_[0]:.4f}", ha='center', va='top', color='black')
        plt.text(ind[74], min(val) - 0.05, f"{lr_model_F3.coef_[0]:.4f}", ha='center', va='top', color='black')

        # 파일 저장
        plt.legend(loc='upper left', bbox_to_anchor=(1,1))
        plt.savefig(f'./SSP585_ASOS/DATA/{city}/{name}.png', bbox_inches='tight')
        plt.clf()

    factors_for_coef = {'SU': SU25,
                'ID': ID0, 
                'FD': FD0,
                'TR': TR20,
                'CDD': CDD,
                'CWD': CWD,
                'TXX': TXX,
                'TXN': TXN,
                'TNX': TNX,
                'TNN': TNN,
                'TX90p': TX90p,
                'TX10p': TX10p,
                'TN90p': TN90p,
                'TN10p': TN10p,
                'R10': R10,
                'R20': R20,
                'R72': R72,    
                'R100': R100,
                'RX1day': RX1day, 
                'RX5day': RX5day, 
                'R95P': R95P, 
                'R99P': R99P, 
                'PRCPTOT': PRCPTOT, 
                'SDII': SDII,
                'DTR': DTR}
    df_coef = pd.DataFrame(columns=factors_for_coef.keys())
    F1,F2,F3 = {},{},{}
    for k in factors_for_coef.keys():
        F1[k] = list()
        F2[k] = list()
        F3[k] = list()
    F1['station'] = city
    F2['station'] = city
    F3['station'] = city
    F1['duration'] = '단기'
    F2['duration'] = '중기'
    F3['duration'] = '장기'
    for k,v in factors_for_coef.items():
        f1,f2,f3 = get_coef(v)
        F1[k].append(f1)
        F2[k].append(f2)
        F3[k].append(f3)

    df_coef_1 = pd.DataFrame(F1)
    df_coef_2 = pd.DataFrame(F2)
    df_coef_3 = pd.DataFrame(F3)
    df_coef = pd.concat([df_coef,df_coef_1,df_coef_2,df_coef_3], ignore_index=True)
    df_coef = df_coef[['station', 'duration', 'SU', 'ID', 'FD', 'TR', 'CDD', 'CWD', 'TXX', 'TXN', 'TNX', 'TNN', 'TX90p', 'TX10p', 'TN90p', 'TN10p', 'R10', 'R20', 'R72', 'R100', 'RX1day', 'RX5day', 'R95P', 'R99P', 'PRCPTOT', 'SDII', 'DTR']]
    df_coef_fin = pd.concat([df_coef_fin,df_coef], ignore_index=True)
    df_coef_fin = df_coef_fin[['station', 'duration', 'SU', 'ID', 'FD', 'TR', 'CDD', 'CWD', 'TXX', 'TXN', 'TNX', 'TNN', 'TX90p', 'TX10p', 'TN90p', 'TN10p', 'R10', 'R20', 'R72', 'R100', 'RX1day', 'RX5day', 'R95P', 'R99P', 'PRCPTOT', 'SDII', 'DTR']]
    
df_coef_fin.to_csv('./GIS.csv',index=False,encoding='utf-8 sig')


C:\Users\CH\AppData\Local\Temp\ipykernel_25912\1783121094.py:50: FutureWarning: Series.__getitem__ treating keys as positions is deprecated. In a future version, integer keys will always be treated as labels (consistent with DataFrame behavior). To access a value by position, use `ser.iloc[pos]`
  CDD=df.groupby(df['YMD'].dt.year)['RN'].apply(lambda x: (x < 1).astype(int).groupby((x >= 1).astype(int).cumsum()).cumsum().max())
C:\Users\CH\AppData\Local\Temp\ipykernel_25912\1783121094.py:50: FutureWarning: Series.__getitem__ treating keys as positions is deprecated. In a future version, integer keys will always be treated as labels (consistent with DataFrame behavior). To access a value by position, use `ser.iloc[pos]`
  CDD=df.groupby(df['YMD'].dt.year)['RN'].apply(lambda x: (x < 1).astype(int).groupby((x >= 1).astype(int).cumsum()).cumsum().max())
C:\Users\CH\AppData\Local\Temp\ipykernel_25912\1783121094.py:50: FutureWarning: Series.__getitem__ treating keys as positions is deprecated.

<Figure size 800x500 with 0 Axes>

<Figure size 800x500 with 0 Axes>

<Figure size 800x500 with 0 Axes>

<Figure size 800x500 with 0 Axes>

...

<Figure size 800x500 with 0 Axes>

<Figure size 800x500 with 0 Axes>

<Figure size 800x500 with 0 Axes>

<Figure size 800x500 with 0 Axes>

<Figure size 800x500 with 0 Axes>

In [24]:
path = f'./SSP585_ASOS/DATA/서울.csv'
# columns = ['YR','MM','DD','RN','TMAX','TMIN']
daterange=('2021', '2100')
# nan values( if 1, then nan values will drop, if 0, then nan values will be replaced by backward fill or forward fill, if -1, program will stop)
nan_set=1
# RNN파라미터
user_defined_precipitation_threshold=10

df = pd.read_csv(path)
df['년-월-일'] = pd.to_datetime(df['년-월-일'])

df['YR'] = df['년-월-일'].dt.year
df['MM'] = df['년-월-일'].dt.month
df['DD'] = df['년-월-일'].dt.day
df = df.drop(['년-월-일'],axis=1)
df = df[['YR','MM','DD','RN','RHM','SI','TA','TAMAX','TAMIN','WS']]
df_qc = qcEtccdi(df,daterange,nan_set)
df = df_qc.copy()

SU25=df.groupby(df['YMD'].dt.year)['TAMAX'].apply(lambda x: (x > 25).sum())
ID0=df.groupby(df['YMD'].dt.year)['TAMAX'].apply(lambda x: (x < 0).sum())
TXN=df.groupby([df['YR'],df['MM']])['TAMAX'].min()
TXX=df.groupby([df['YR'],df['MM']])['TAMAX'].max()
TX10p=df.groupby([df['YR'],df['MM']])['TAMAX'].quantile(0.1)
TX90p=df.groupby([df['YR'],df['MM']])['TAMAX'].quantile(0.9)
# WSDI

# var: TAMIN
FD0=df.groupby(df['YMD'].dt.year)['TAMIN'].apply(lambda x: (x < 0).sum())
TR20=df.groupby(df['YMD'].dt.year)['TAMIN'].apply(lambda x: (x > 20).sum())
TNN=df.groupby([df['YR'],df['MM']])['TAMIN'].min()
TNX=df.groupby([df['YR'],df['MM']])['TAMIN'].max()
TN10p=df.groupby([df['YR'],df['MM']])['TAMIN'].quantile(0.1)
TN90p=df.groupby([df['YR'],df['MM']])['TAMIN'].quantile(0.9)
# CSDI

# TAMAX TAMIN
DTR=df.groupby([df['YR'],df['MM']])['TAMAX'].mean()-df.groupby([df['YR'],df['MM']])['TAMIN'].mean()
# GSL

# var: PRCP
CDD=df.groupby(df['YMD'].dt.year)['RN'].apply(lambda x: (x < 1).astype(int).groupby((x >= 1).astype(int).cumsum()).cumsum().max())
CWD=df.groupby(df['YMD'].dt.year)['RN'].apply(lambda x: (x >= 1).astype(int).groupby((x < 1).astype(int).cumsum()).cumsum().max())
PRCPTOT=df.groupby(df['YMD'].dt.year)['RN'].sum()
RX1day=df.groupby([df['YR'],df['MM']])['RN'].max()
RX5day=df.groupby([df['YR'],df['MM']])['RN'].rolling(5).sum()
R95P=df.groupby([df['YR'],df['MM']])['RN'].quantile(0.95)
R99P=df.groupby([df['YR'],df['MM']])['RN'].quantile(0.99)
SDII=df.groupby(df['YMD'].dt.year)['RN'].sum() / (df.groupby(df['YMD'].dt.year)['RN'].apply(lambda x: (x > 1).sum()))
RNN=df.groupby(df['YMD'].dt.year)['RN'].apply(lambda x: (x < user_defined_precipitation_threshold).sum())
R10=df.groupby(df['YMD'].dt.year)['RN'].apply(lambda x: (x > 10).sum())
R20=df.groupby(df['YMD'].dt.year)['RN'].apply(lambda x: (x > 20).sum())
R72=df.groupby(df['YMD'].dt.year)['RN'].apply(lambda x: (x > 72).sum())
R100=df.groupby(df['YMD'].dt.year)['RN'].apply(lambda x: (x > 100).sum())

C:\Users\scsc0\AppData\Local\Temp\ipykernel_23548\985231081.py:42: FutureWarning: Series.__getitem__ treating keys as positions is deprecated. In a future version, integer keys will always be treated as labels (consistent with DataFrame behavior). To access a value by position, use `ser.iloc[pos]`
  CDD=df.groupby(df['YMD'].dt.year)['RN'].apply(lambda x: (x < 1).astype(int).groupby((x >= 1).astype(int).cumsum()).cumsum().max())
C:\Users\scsc0\AppData\Local\Temp\ipykernel_23548\985231081.py:42: FutureWarning: Series.__getitem__ treating keys as positions is deprecated. In a future version, integer keys will always be treated as labels (consistent with DataFrame behavior). To access a value by position, use `ser.iloc[pos]`
  CDD=df.groupby(df['YMD'].dt.year)['RN'].apply(lambda x: (x < 1).astype(int).groupby((x >= 1).astype(int).cumsum()).cumsum().max())
C:\Users\scsc0\AppData\Local\Temp\ipykernel_23548\985231081.py:42: FutureWarning: Series.__getitem__ treating keys as positions is depre

In [25]:
# txx 따로 그려지나 
data_list = ['RHM', 'RN', 'SI', 'TA', 'TAMAX', 'TAMIN', 'WS']
city = 'total'

# law 데이터 평균값 구해서 DF 로 합치기
ddf = pd.DataFrame()
for data_type in data_list:
    path = f'./SSP585_ASOS/concat_data/{data_type}.csv'
    df = pd.read_csv(path)
    df[f'{data_type}'] = df[df.columns[1:]].mean(axis=1)
    dff = df[f'{data_type}']
    ddf = pd.concat([ddf,dff],axis=1)

daterange=('2021', '2100')
# nan values( if 1, then nan values will drop, if 0, then nan values will be replaced by backward fill or forward fill, if -1, program will stop)
nan_set=1
# RNN파라미터
user_defined_precipitation_threshold=10

df['년-월-일'] = pd.to_datetime(df['년-월-일'])
ddf['YR'] = df['년-월-일'].dt.year
ddf['MM'] = df['년-월-일'].dt.month
ddf['DD'] = df['년-월-일'].dt.day
# ddf = ddf.drop(['년-월-일'],axis=1)
ddf = ddf[['YR','MM','DD','RN','RHM','SI','TA','TAMAX','TAMIN','WS']]
df_qc = qcEtccdi(ddf,daterange,nan_set)
df = df_qc.copy()

SU25=df.groupby(df['YMD'].dt.year)['TAMAX'].apply(lambda x: (x > 25).sum())
ID0=df.groupby(df['YMD'].dt.year)['TAMAX'].apply(lambda x: (x < 0).sum())
TXN=df.groupby([df['YR'],df['MM']])['TAMAX'].min()
TXX=df.groupby([df['YR'],df['MM']])['TAMAX'].max()
TX10p=df.groupby([df['YR'],df['MM']])['TAMAX'].quantile(0.1)
TX90p=df.groupby([df['YR'],df['MM']])['TAMAX'].quantile(0.9)
# WSDI

# var: TAMIN
FD0=df.groupby(df['YMD'].dt.year)['TAMIN'].apply(lambda x: (x < 0).sum())
TR20=df.groupby(df['YMD'].dt.year)['TAMIN'].apply(lambda x: (x > 20).sum())
TNN=df.groupby([df['YR'],df['MM']])['TAMIN'].min()
TNX=df.groupby([df['YR'],df['MM']])['TAMIN'].max()
TN10p=df.groupby([df['YR'],df['MM']])['TAMIN'].quantile(0.1)
TN90p=df.groupby([df['YR'],df['MM']])['TAMIN'].quantile(0.9)
# CSDI

# TAMAX TAMIN
DTR=df.groupby([df['YR'],df['MM']])['TAMAX'].mean()-df.groupby([df['YR'],df['MM']])['TAMIN'].mean()
# GSL

# var: PRCP
CDD=df.groupby(df['YMD'].dt.year)['RN'].apply(lambda x: (x < 1).astype(int).groupby((x >= 1).astype(int).cumsum()).cumsum().max())
CWD=df.groupby(df['YMD'].dt.year)['RN'].apply(lambda x: (x >= 1).astype(int).groupby((x < 1).astype(int).cumsum()).cumsum().max())
PRCPTOT=df.groupby(df['YMD'].dt.year)['RN'].sum()
RX1day=df.groupby([df['YR'],df['MM']])['RN'].max()
RX5day=df.groupby([df['YR'],df['MM']])['RN'].rolling(5).sum()
R95P=df.groupby([df['YR'],df['MM']])['RN'].quantile(0.95)
R99P=df.groupby([df['YR'],df['MM']])['RN'].quantile(0.99)
SDII=df.groupby(df['YMD'].dt.year)['RN'].sum() / (df.groupby(df['YMD'].dt.year)['RN'].apply(lambda x: (x > 1).sum()))
RNN=df.groupby(df['YMD'].dt.year)['RN'].apply(lambda x: (x < user_defined_precipitation_threshold).sum())
R10=df.groupby(df['YMD'].dt.year)['RN'].apply(lambda x: (x > 10).sum())
R20=df.groupby(df['YMD'].dt.year)['RN'].apply(lambda x: (x > 20).sum())
R72=df.groupby(df['YMD'].dt.year)['RN'].apply(lambda x: (x > 72).sum())
R100=df.groupby(df['YMD'].dt.year)['RN'].apply(lambda x: (x > 100).sum())

## 이미지 그리기
# TXx, TNx, TNx, TNn 그리기
plt.figure(figsize=(8,5))

ind_TXX=TXX.groupby(TXX.index.get_level_values(0)).max().index
val_TXX=TXX.groupby(TXX.index.get_level_values(0)).max().values

plt.plot(ind_TXX,val_TXX,color = '#FE0000',label='TXx')

plt.grid()
plt.title('TXx')
plt.xlabel('Year')
plt.ylabel('Temp(℃)')
plt.legend(loc='upper left', bbox_to_anchor=(1,1))
if not os.path.isdir(f'./SSP585_ASOS/DATA/{city}'):
    os.makedirs(f'./SSP585_ASOS/DATA/{city}')
    plt.savefig(f'./SSP585_ASOS/DATA/{city}/TXx.png', bbox_inches='tight')

# 이미지 저장
plt.savefig(f'./SSP585_ASOS/DATA/{city}/TA.png', bbox_inches='tight')

ind_TNX=TNX.groupby(TNX.index.get_level_values(0)).max().index
val_TNX=TNX.groupby(TNX.index.get_level_values(0)).max().values

plt.plot(ind_TNX,val_TNX,color = '#EA7676', label='TNx')

ind_TXN=TXN.groupby(TXN.index.get_level_values(0)).min().index
val_TXN=TXN.groupby(TXN.index.get_level_values(0)).min().values

plt.plot(ind_TXN,val_TXN,color = '#6FA2ED', label='TXn')

ind_TNN=TNN.groupby(TNN.index.get_level_values(0)).min().index
val_TNN=TNN.groupby(TNN.index.get_level_values(0)).min().values

plt.plot(ind_TNN,val_TNN,color = '#1E00FE', label='TNn')

# 그래프 정보 넣기
plt.grid()
plt.title('TXx,TXn,TNx,TNn')
plt.xlabel('Year')
plt.ylabel('Temp(℃)')
plt.legend(loc='upper left', bbox_to_anchor=(1,1))
if not os.path.isdir(f'./SSP585_ASOS/DATA/{city}'):
    os.makedirs(f'./SSP585_ASOS/DATA/{city}')

# 이미지 저장
plt.savefig(f'./SSP585_ASOS/DATA/{city}/TA.png', bbox_inches='tight')

# 이미지 초기화
plt.clf()

C:\Users\scsc0\AppData\Local\Temp\ipykernel_23548\1074865458.py:51: FutureWarning: Series.__getitem__ treating keys as positions is deprecated. In a future version, integer keys will always be treated as labels (consistent with DataFrame behavior). To access a value by position, use `ser.iloc[pos]`
  CDD=df.groupby(df['YMD'].dt.year)['RN'].apply(lambda x: (x < 1).astype(int).groupby((x >= 1).astype(int).cumsum()).cumsum().max())
C:\Users\scsc0\AppData\Local\Temp\ipykernel_23548\1074865458.py:51: FutureWarning: Series.__getitem__ treating keys as positions is deprecated. In a future version, integer keys will always be treated as labels (consistent with DataFrame behavior). To access a value by position, use `ser.iloc[pos]`
  CDD=df.groupby(df['YMD'].dt.year)['RN'].apply(lambda x: (x < 1).astype(int).groupby((x >= 1).astype(int).cumsum()).cumsum().max())
C:\Users\scsc0\AppData\Local\Temp\ipykernel_23548\1074865458.py:51: FutureWarning: Series.__getitem__ treating keys as positions is de

<Figure size 800x500 with 0 Axes>

In [26]:
# txx 따로 그려지나 0920 수정본
data_list = ['RHM', 'RN', 'SI', 'TA', 'TAMAX', 'TAMIN', 'WS']
city = 'total'

# law 데이터 평균값 구해서 DF 로 합치기
ddf = pd.DataFrame()
for data_type in data_list:
    path = f'./SSP585_ASOS/concat_data/{data_type}.csv'
    df = pd.read_csv(path)
    df[f'{data_type}'] = df[df.columns[1:]].mean(axis=1)
    dff = df[f'{data_type}']
    ddf = pd.concat([ddf,dff],axis=1)

daterange=('2021', '2100')
# nan values( if 1, then nan values will drop, if 0, then nan values will be replaced by backward fill or forward fill, if -1, program will stop)
nan_set=1
# RNN파라미터
user_defined_precipitation_threshold=10

df['년-월-일'] = pd.to_datetime(df['년-월-일'])
ddf['YR'] = df['년-월-일'].dt.year
ddf['MM'] = df['년-월-일'].dt.month
ddf['DD'] = df['년-월-일'].dt.day
# ddf = ddf.drop(['년-월-일'],axis=1)
ddf = ddf[['YR','MM','DD','RN','RHM','SI','TA','TAMAX','TAMIN','WS']]
df_qc = qcEtccdi(ddf,daterange,nan_set)
df = df_qc.copy()

SU25=df.groupby(df['YMD'].dt.year)['TAMAX'].apply(lambda x: (x > 25).sum())
ID0=df.groupby(df['YMD'].dt.year)['TAMAX'].apply(lambda x: (x < 0).sum())
TXN=df.groupby([df['YR'],df['MM']])['TAMAX'].min()
TXX=df.groupby([df['YR'],df['MM']])['TAMAX'].max()
TX10p=df.groupby([df['YR'],df['MM']])['TAMAX'].quantile(0.1)
TX90p=df.groupby([df['YR'],df['MM']])['TAMAX'].quantile(0.9)
# WSDI

# var: TAMIN
FD0=df.groupby(df['YMD'].dt.year)['TAMIN'].apply(lambda x: (x < 0).sum())
TR20=df.groupby(df['YMD'].dt.year)['TAMIN'].apply(lambda x: (x > 20).sum())
TNN=df.groupby([df['YR'],df['MM']])['TAMIN'].min()
TNX=df.groupby([df['YR'],df['MM']])['TAMIN'].max()
TN10p=df.groupby([df['YR'],df['MM']])['TAMIN'].quantile(0.1)
TN90p=df.groupby([df['YR'],df['MM']])['TAMIN'].quantile(0.9)
# CSDI

# TAMAX TAMIN
DTR=df.groupby([df['YR'],df['MM']])['TAMAX'].mean()-df.groupby([df['YR'],df['MM']])['TAMIN'].mean()
# GSL

# var: PRCP
CDD=df.groupby(df['YMD'].dt.year)['RN'].apply(lambda x: (x < 1).astype(int).groupby((x >= 1).astype(int).cumsum()).cumsum().max())
CWD=df.groupby(df['YMD'].dt.year)['RN'].apply(lambda x: (x >= 1).astype(int).groupby((x < 1).astype(int).cumsum()).cumsum().max())
PRCPTOT=df.groupby(df['YMD'].dt.year)['RN'].sum()
RX1day=df.groupby([df['YR'],df['MM']])['RN'].max()
RX5day=df.groupby([df['YR'],df['MM']])['RN'].rolling(5).sum()
R95P=df.groupby([df['YR'],df['MM']])['RN'].quantile(0.95)
R99P=df.groupby([df['YR'],df['MM']])['RN'].quantile(0.99)
SDII=df.groupby(df['YMD'].dt.year)['RN'].sum() / (df.groupby(df['YMD'].dt.year)['RN'].apply(lambda x: (x > 1).sum()))
RNN=df.groupby(df['YMD'].dt.year)['RN'].apply(lambda x: (x < user_defined_precipitation_threshold).sum())
R10=df.groupby(df['YMD'].dt.year)['RN'].apply(lambda x: (x > 10).sum())
R20=df.groupby(df['YMD'].dt.year)['RN'].apply(lambda x: (x > 20).sum())
R72=df.groupby(df['YMD'].dt.year)['RN'].apply(lambda x: (x > 72).sum())
R100=df.groupby(df['YMD'].dt.year)['RN'].apply(lambda x: (x > 100).sum())

## 이미지 그리기
# TXx, TNx, TNx, TNn 그리기
plt.figure(figsize=(8,5))

ind_TXX = TXX.groupby(TXX.index.get_level_values(0)).max().index
val_TXX = TXX.groupby(TXX.index.get_level_values(0)).max().values

plt.plot(ind_TXX, val_TXX, color='#FE0000', label='TXx')

plt.grid()
plt.title('TXx')
plt.xlabel('Year')
plt.ylabel('Temp(℃)')
plt.legend(loc='upper left', bbox_to_anchor=(1,1))
if not os.path.isdir(f'./SSP585_ASOS/DATA/{city}'):
    os.makedirs(f'./SSP585_ASOS/DATA/{city}')
plt.savefig(f'./SSP585_ASOS/DATA/{city}/TXx.png', bbox_inches='tight')

# Clear the plot
plt.clf()

# TNx 그리기
ind_TNX = TNX.groupby(TNX.index.get_level_values(0)).max().index
val_TNX = TNX.groupby(TNX.index.get_level_values(0)).max().values

plt.plot(ind_TNX, val_TNX, color='#EA7676', label='TNx')

plt.grid()
plt.title('TNx')
plt.xlabel('Year')
plt.ylabel('Temp(℃)')
plt.legend(loc='upper left', bbox_to_anchor=(1,1))
if not os.path.isdir(f'./SSP585_ASOS/DATA/{city}'):
    os.makedirs(f'./SSP585_ASOS/DATA/{city}')
plt.savefig(f'./SSP585_ASOS/DATA/{city}/TNx.png', bbox_inches='tight')

# Clear the plot
plt.clf()

# TXn 그리기
ind_TXN = TXN.groupby(TXN.index.get_level_values(0)).min().index
val_TXN = TXN.groupby(TXN.index.get_level_values(0)).min().values

plt.plot(ind_TXN, val_TXN, color='#6FA2ED', label='TXn')

plt.grid()
plt.title('TXn')
plt.xlabel('Year')
plt.ylabel('Temp(℃)')
plt.legend(loc='upper left', bbox_to_anchor=(1,1))
if not os.path.isdir(f'./SSP585_ASOS/DATA/{city}'):
    os.makedirs(f'./SSP585_ASOS/DATA/{city}')
plt.savefig(f'./SSP585_ASOS/DATA/{city}/TXn.png', bbox_inches='tight')

# Clear the plot
plt.clf()

# TNn 그리기
ind_TNN = TNN.groupby(TNN.index.get_level_values(0)).min().index
val_TNN = TNN.groupby(TNN.index.get_level_values(0)).min().values

plt.plot(ind_TNN, val_TNN, color='#1E00FE', label='TNn')

plt.grid()
plt.title('TNn')
plt.xlabel('Year')
plt.ylabel('Temp(℃)')
plt.legend(loc='upper left', bbox_to_anchor=(1,1))
if not os.path.isdir(f'./SSP585_ASOS/DATA/{city}'):
    os.makedirs(f'./SSP585_ASOS/DATA/{city}')
plt.savefig(f'./SSP585_ASOS/DATA/{city}/TNn.png', bbox_inches='tight')

# Clear the plot
plt.clf()

# 온도지수 4개 한꺼번에 표현
plt.figure(figsize=(8,5))

ind_TXX=TXX.groupby(TXX.index.get_level_values(0)).max().index
val_TXX=TXX.groupby(TXX.index.get_level_values(0)).max().values

plt.plot(ind_TXX,val_TXX,color = '#FE0000',label='TXx')

ind_TNX=TNX.groupby(TNX.index.get_level_values(0)).max().index
val_TNX=TNX.groupby(TNX.index.get_level_values(0)).max().values

plt.plot(ind_TNX,val_TNX,color = '#EA7676', label='TNx')

ind_TXN=TXN.groupby(TXN.index.get_level_values(0)).min().index
val_TXN=TXN.groupby(TXN.index.get_level_values(0)).min().values

plt.plot(ind_TXN,val_TXN,color = '#6FA2ED', label='TXn')

ind_TNN=TNN.groupby(TNN.index.get_level_values(0)).min().index
val_TNN=TNN.groupby(TNN.index.get_level_values(0)).min().values

plt.plot(ind_TNN,val_TNN,color = '#1E00FE', label='TNn')

# 그래프 정보 넣기
plt.grid()
plt.title('TXx,TXn,TNx,TNn')
plt.xlabel('Year')
plt.ylabel('Temp(℃)')
plt.legend(loc='upper left', bbox_to_anchor=(1,1))
if not os.path.isdir(f'./SSP585_ASOS/DATA/{city}'):
    os.makedirs(f'./SSP585_ASOS/DATA/{city}')

# 이미지 저장
plt.savefig(f'./SSP585_ASOS/DATA/{city}/TA.png', bbox_inches='tight')

# 이미지 초기화
plt.clf()


# TX10, TX90 그리기
ind_TX10p=TX10p.groupby(TX10p.index.get_level_values(0)).max().index
val_TX10p=TX10p.groupby(TX10p.index.get_level_values(0)).max().values

plt.plot(ind_TX10p,val_TX10p,color = 'r',label='TX10p')

ind_TX90p=TX90p.groupby(TX90p.index.get_level_values(0)).max().index
val_TX90p=TX90p.groupby(TX90p.index.get_level_values(0)).max().values

plt.plot(ind_TX90p,val_TX90p,color = 'b',label='TX90p')

# 두 그래프 사이 칠하기
plt.fill_between(ind_TX90p,val_TX10p,val_TX90p, color='gray', alpha=0.3)
plt.legend()
plt.grid()
plt.xlabel('year')
plt.ylabel('Temp(℃)')
plt.title('TX10,90P')

# 이미지 저장
plt.savefig(f'./SSP585_ASOS/DATA/{city}/TX10,90P.png', bbox_inches='tight')

# 이미지 초기화
plt.clf()

# TN10, TN90 그리기
ind_TN10p=TN10p.groupby(TN10p.index.get_level_values(0)).max().index
val_TN10p=TN10p.groupby(TN10p.index.get_level_values(0)).max().values

plt.plot(ind_TN10p,val_TN10p,color = 'r',label='TN10p')

ind_TN90p=TN90p.groupby(TN90p.index.get_level_values(0)).max().index
val_TN90p=TN90p.groupby(TN90p.index.get_level_values(0)).max().values

plt.plot(ind_TN90p,val_TN90p,color = 'b',label='TN90p')

# 두 그래프 사이 칠하기
plt.fill_between(ind_TN90p,val_TN10p,val_TN90p, color='gray', alpha=0.3)
plt.legend()
plt.grid()
plt.title('TN10,90P')
plt.xlabel('year')
plt.ylabel('Temp(℃)')

# 이미지 저장
plt.savefig(f'./SSP585_ASOS/DATA/{city}/TN10,90P.png', bbox_inches='tight')

# 이미지 초기화
plt.clf()

# SU ID FD TR CDD CWD Rx1day R20 그리기
mm = ['RX1day', 'RX5day', 'R95P', 'R99P', 'PRCPTOT', 'SDII']
factors = {'SU': SU25, # day
        'ID': ID0, #
        'FD': FD0,
        'TR': TR20,
        'CDD': CDD,
        'CWD': CWD,
        'R10': R10,
        'R20': R20,  # day
        'R72': R72,
        'R100': R100,
        'RX1day': RX1day, # mm
        'RX5day': RX5day, # mm
        'R95P': R95P, # mm
        'R99P': R99P, # mm 
        'PRCPTOT': PRCPTOT, # mm
        'SDII': SDII,  # mm
        'DTR': DTR} # ℃
for name,item in factors.items():
    
    ind=item.groupby(item.index.get_level_values(0)).max().index
    val=item.groupby(item.index.get_level_values(0)).max().values

    # 그래프 그리기
    plt.plot(ind,val,color = 'r',label=name)

    # 그래프 정보 넣기
    plt.title(name)
    plt.grid()
    plt.xlabel('year')
    if name in mm:
        plt.ylabel('mm')
    elif name == 'DTR':
        plt.ylabel('Temp(℃)')
    else:
        plt.ylabel('day')

    # 추세선 그리기
    lr_model_F1=LR()
    lr_model_F2=LR()
    lr_model_F3=LR()
    
    lr_model_F1.fit(ind.values.reshape(-1,1)[:30], val[:30])
    lr_model_F1.coef_

    lr_model_F2.fit(ind.values.reshape(-1,1)[30:60], val[30:60])
    lr_model_F2.coef_

    lr_model_F3.fit(ind.values.reshape(-1,1)[60:], val[60:])
    lr_model_F3.coef_

    plt.plot(ind[:30],lr_model_F1.predict(ind.values.reshape(-1,1)[:30]), color='b',lw=0.8,label='trend line')
    plt.plot(ind[30:60],lr_model_F2.predict(ind.values.reshape(-1,1)[30:60]), color='b',lw=0.8)
    plt.plot(ind[60:],lr_model_F3.predict(ind.values.reshape(-1,1)[60:]), color='b',lw=0.8)

    plt.text(ind[14], min(val) - 0.05, f"{lr_model_F1.coef_[0]:.4f}", ha='center', va='top', color='black')
    plt.text(ind[44], min(val) - 0.05, f"{lr_model_F2.coef_[0]:.4f}", ha='center', va='top', color='black')
    plt.text(ind[74], min(val) - 0.05, f"{lr_model_F3.coef_[0]:.4f}", ha='center', va='top', color='black')

    # 파일 저장
    plt.legend(loc='upper left', bbox_to_anchor=(1,1))
    plt.savefig(f'./SSP585_ASOS/DATA/{city}/{name}.png', bbox_inches='tight')
    plt.clf()

C:\Users\scsc0\AppData\Local\Temp\ipykernel_23548\3473825928.py:51: FutureWarning: Series.__getitem__ treating keys as positions is deprecated. In a future version, integer keys will always be treated as labels (consistent with DataFrame behavior). To access a value by position, use `ser.iloc[pos]`
  CDD=df.groupby(df['YMD'].dt.year)['RN'].apply(lambda x: (x < 1).astype(int).groupby((x >= 1).astype(int).cumsum()).cumsum().max())
C:\Users\scsc0\AppData\Local\Temp\ipykernel_23548\3473825928.py:51: FutureWarning: Series.__getitem__ treating keys as positions is deprecated. In a future version, integer keys will always be treated as labels (consistent with DataFrame behavior). To access a value by position, use `ser.iloc[pos]`
  CDD=df.groupby(df['YMD'].dt.year)['RN'].apply(lambda x: (x < 1).astype(int).groupby((x >= 1).astype(int).cumsum()).cumsum().max())
C:\Users\scsc0\AppData\Local\Temp\ipykernel_23548\3473825928.py:51: FutureWarning: Series.__getitem__ treating keys as positions is de

<Figure size 800x500 with 0 Axes>

<Figure size 800x500 with 0 Axes>

In [27]:
# ## 전 지역(ASOS95개소) 평균 지수 구하기
# data_list = ['RHM', 'RN', 'SI', 'TA', 'TAMAX', 'TAMIN', 'WS']
# city = 'total'

# # law 데이터 평균값 구해서 DF 로 합치기
# ddf = pd.DataFrame()
# for data_type in data_list:
#     path = f'./SSP585_ASOS/concat_data/{data_type}.csv'
#     df = pd.read_csv(path)
#     df[f'{data_type}'] = df[df.columns[1:]].mean(axis=1)
#     dff = df[f'{data_type}']
#     ddf = pd.concat([ddf,dff],axis=1)

# daterange=('2021', '2100')
# # nan values( if 1, then nan values will drop, if 0, then nan values will be replaced by backward fill or forward fill, if -1, program will stop)
# nan_set=1
# # RNN파라미터
# user_defined_precipitation_threshold=10

# df['년-월-일'] = pd.to_datetime(df['년-월-일'])
# ddf['YR'] = df['년-월-일'].dt.year
# ddf['MM'] = df['년-월-일'].dt.month
# ddf['DD'] = df['년-월-일'].dt.day
# # ddf = ddf.drop(['년-월-일'],axis=1)
# ddf = ddf[['YR','MM','DD','RN','RHM','SI','TA','TAMAX','TAMIN','WS']]
# df_qc = qcEtccdi(ddf,daterange,nan_set)
# df = df_qc.copy()

# SU25=df.groupby(df['YMD'].dt.year)['TAMAX'].apply(lambda x: (x > 25).sum())
# ID0=df.groupby(df['YMD'].dt.year)['TAMAX'].apply(lambda x: (x < 0).sum())
# TXN=df.groupby([df['YR'],df['MM']])['TAMAX'].min()
# TXX=df.groupby([df['YR'],df['MM']])['TAMAX'].max()
# TX10p=df.groupby([df['YR'],df['MM']])['TAMAX'].quantile(0.1)
# TX90p=df.groupby([df['YR'],df['MM']])['TAMAX'].quantile(0.9)
# # WSDI

# # var: TAMIN
# FD0=df.groupby(df['YMD'].dt.year)['TAMIN'].apply(lambda x: (x < 0).sum())
# TR20=df.groupby(df['YMD'].dt.year)['TAMIN'].apply(lambda x: (x > 20).sum())
# TNN=df.groupby([df['YR'],df['MM']])['TAMIN'].min()
# TNX=df.groupby([df['YR'],df['MM']])['TAMIN'].max()
# TN10p=df.groupby([df['YR'],df['MM']])['TAMIN'].quantile(0.1)
# TN90p=df.groupby([df['YR'],df['MM']])['TAMIN'].quantile(0.9)
# # CSDI

# # TAMAX TAMIN
# DTR=df.groupby([df['YR'],df['MM']])['TAMAX'].mean()-df.groupby([df['YR'],df['MM']])['TAMIN'].mean()
# # GSL

# # var: PRCP
# CDD=df.groupby(df['YMD'].dt.year)['RN'].apply(lambda x: (x < 1).astype(int).groupby((x >= 1).astype(int).cumsum()).cumsum().max())
# CWD=df.groupby(df['YMD'].dt.year)['RN'].apply(lambda x: (x >= 1).astype(int).groupby((x < 1).astype(int).cumsum()).cumsum().max())
# PRCPTOT=df.groupby(df['YMD'].dt.year)['RN'].sum()
# RX1day=df.groupby([df['YR'],df['MM']])['RN'].max()
# RX5day=df.groupby([df['YR'],df['MM']])['RN'].rolling(5).sum()
# R95P=df.groupby([df['YR'],df['MM']])['RN'].quantile(0.95)
# R99P=df.groupby([df['YR'],df['MM']])['RN'].quantile(0.99)
# SDII=df.groupby(df['YMD'].dt.year)['RN'].sum() / (df.groupby(df['YMD'].dt.year)['RN'].apply(lambda x: (x > 1).sum()))
# RNN=df.groupby(df['YMD'].dt.year)['RN'].apply(lambda x: (x < user_defined_precipitation_threshold).sum())
# R10=df.groupby(df['YMD'].dt.year)['RN'].apply(lambda x: (x > 10).sum())
# R20=df.groupby(df['YMD'].dt.year)['RN'].apply(lambda x: (x > 20).sum())
# R72=df.groupby(df['YMD'].dt.year)['RN'].apply(lambda x: (x > 72).sum())
# R100=df.groupby(df['YMD'].dt.year)['RN'].apply(lambda x: (x > 100).sum())

# ## 이미지 그리기
# # TXx, TNx, TNx, TNn 그리기
# plt.figure(figsize=(8,5))

# ind_TXX=TXX.groupby(TXX.index.get_level_values(0)).max().index
# val_TXX=TXX.groupby(TXX.index.get_level_values(0)).max().values

# plt.plot(ind_TXX,val_TXX,color = '#FE0000',label='TXx')

# ind_TNX=TNX.groupby(TNX.index.get_level_values(0)).max().index
# val_TNX=TNX.groupby(TNX.index.get_level_values(0)).max().values

# plt.plot(ind_TNX,val_TNX,color = '#EA7676', label='TNx')

# ind_TXN=TXN.groupby(TXN.index.get_level_values(0)).min().index
# val_TXN=TXN.groupby(TXN.index.get_level_values(0)).min().values

# plt.plot(ind_TXN,val_TXN,color = '#6FA2ED', label='TXn')

# ind_TNN=TNN.groupby(TNN.index.get_level_values(0)).min().index
# val_TNN=TNN.groupby(TNN.index.get_level_values(0)).min().values

# plt.plot(ind_TNN,val_TNN,color = '#1E00FE', label='TNn')

# # 그래프 정보 넣기
# plt.grid()
# plt.title('TXx,TXn,TNx,TNn')
# plt.xlabel('Year')
# plt.ylabel('Temp(℃)')
# plt.legend(loc='upper left', bbox_to_anchor=(1,1))
# if not os.path.isdir(f'./SSP585_ASOS/DATA/{city}'):
#     os.makedirs(f'./SSP585_ASOS/DATA/{city}')

# # 이미지 저장
# plt.savefig(f'./SSP585_ASOS/DATA/{city}/TA.png', bbox_inches='tight')

# # 이미지 초기화
# plt.clf()

# # TX10, TX90 그리기
# ind_TX10p=TX10p.groupby(TX10p.index.get_level_values(0)).max().index
# val_TX10p=TX10p.groupby(TX10p.index.get_level_values(0)).max().values

# plt.plot(ind_TX10p,val_TX10p,color = 'r',label='TX10p')

# ind_TX90p=TX90p.groupby(TX90p.index.get_level_values(0)).max().index
# val_TX90p=TX90p.groupby(TX90p.index.get_level_values(0)).max().values

# plt.plot(ind_TX90p,val_TX90p,color = 'b',label='TX90p')

# # 두 그래프 사이 칠하기
# plt.fill_between(ind_TX90p,val_TX10p,val_TX90p, color='gray', alpha=0.3)
# plt.legend()
# plt.grid()
# plt.xlabel('year')
# plt.ylabel('Temp(℃)')
# plt.title('TX10,90P')

# # 이미지 저장
# plt.savefig(f'./SSP585_ASOS/DATA/{city}/TX10,90P.png', bbox_inches='tight')

# # 이미지 초기화
# plt.clf()

# # TN10, TN90 그리기
# ind_TN10p=TN10p.groupby(TN10p.index.get_level_values(0)).max().index
# val_TN10p=TN10p.groupby(TN10p.index.get_level_values(0)).max().values

# plt.plot(ind_TN10p,val_TN10p,color = 'r',label='TN10p')

# ind_TN90p=TN90p.groupby(TN90p.index.get_level_values(0)).max().index
# val_TN90p=TN90p.groupby(TN90p.index.get_level_values(0)).max().values

# plt.plot(ind_TN90p,val_TN90p,color = 'b',label='TN90p')

# # 두 그래프 사이 칠하기
# plt.fill_between(ind_TN90p,val_TN10p,val_TN90p, color='gray', alpha=0.3)
# plt.legend()
# plt.grid()
# plt.title('TN10,90P')
# plt.xlabel('year')
# plt.ylabel('Temp(℃)')

# # 이미지 저장
# plt.savefig(f'./SSP585_ASOS/DATA/{city}/TN10,90P.png', bbox_inches='tight')

# # 이미지 초기화
# plt.clf()

# # SU ID FD TR CDD CWD Rx1day R20 그리기
# mm = ['RX1day', 'RX5day', 'R95P', 'R99P', 'PRCPTOT', 'SDII']
# factors = {'SU': SU25, # day
#         'ID': ID0, #
#         'FD': FD0,
#         'TR': TR20,
#         'CDD': CDD,
#         'CWD': CWD,
#         'R10': R10,
#         'R20': R20,  # day
#         'R72': R72,
#         'R100': R100,
#         'RX1day': RX1day, # mm
#         'RX5day': RX5day, # mm
#         'R95P': R95P, # mm
#         'R99P': R99P, # mm 
#         'PRCPTOT': PRCPTOT, # mm
#         'SDII': SDII,  # mm
#         'DTR': DTR} # ℃
# for name,item in factors.items():
    
#     ind=item.groupby(item.index.get_level_values(0)).max().index
#     val=item.groupby(item.index.get_level_values(0)).max().values

#     # 그래프 그리기
#     plt.plot(ind,val,color = 'r',label=name)

#     # 그래프 정보 넣기
#     plt.title(name)
#     plt.grid()
#     plt.xlabel('year')
#     if name in mm:
#         plt.ylabel('mm')
#     elif name == 'DTR':
#         plt.ylabel('Temp(℃)')
#     else:
#         plt.ylabel('day')

#     # 추세선 그리기
#     lr_model_F1=LR()
#     lr_model_F2=LR()
#     lr_model_F3=LR()
    
#     lr_model_F1.fit(ind.values.reshape(-1,1)[:30], val[:30])
#     lr_model_F1.coef_

#     lr_model_F2.fit(ind.values.reshape(-1,1)[30:60], val[30:60])
#     lr_model_F2.coef_

#     lr_model_F3.fit(ind.values.reshape(-1,1)[60:], val[60:])
#     lr_model_F3.coef_

#     plt.plot(ind[:30],lr_model_F1.predict(ind.values.reshape(-1,1)[:30]), color='b',lw=0.8,label='trend line')
#     plt.plot(ind[30:60],lr_model_F2.predict(ind.values.reshape(-1,1)[30:60]), color='b',lw=0.8)
#     plt.plot(ind[60:],lr_model_F3.predict(ind.values.reshape(-1,1)[60:]), color='b',lw=0.8)

#     plt.text(ind[14], min(val) - 0.05, f"{lr_model_F1.coef_[0]:.4f}", ha='center', va='top', color='black')
#     plt.text(ind[44], min(val) - 0.05, f"{lr_model_F2.coef_[0]:.4f}", ha='center', va='top', color='black')
#     plt.text(ind[74], min(val) - 0.05, f"{lr_model_F3.coef_[0]:.4f}", ha='center', va='top', color='black')

#     # 파일 저장
#     plt.legend(loc='upper left', bbox_to_anchor=(1,1))
#     plt.savefig(f'./SSP585_ASOS/DATA/{city}/{name}.png', bbox_inches='tight')
#     plt.clf()

In [28]:
RX5day=df.groupby([df['YR'], df['MM']])['RN'].rolling(5).sum()
# MultiIndex를 가진 시리즈에서 YMD를 사용하여 인덱스를 일단위로 정렬
RX5day.index = pd.to_datetime(RX5day.index.get_level_values('YMD'))

# 5일 이동합 계산

# 연도별 RX5day 계산
RX5day = RX5day.groupby(RX5day.index.year).max()

In [2]:
import geopandas as gpd
from shapely.geometry import Point
import pandas as pd
meta = pd.read_csv('./SSP585_ASOS/META_관측지점정보_20240908170443.csv', encoding = 'EUC-KR')
meta = meta[['위도','경도','지점명']]
meta.drop_duplicates('지점명',inplace= True)

etccdi = pd.read_csv('./GIS.csv') 
merged = pd.merge(etccdi,meta,left_on='station', right_on='지점명', how='inner').drop('지점명',axis=1)
merged['geometry'] = merged.apply(lambda row: Point(row['경도'], row['위도']), axis=1)
geo_df = gpd.GeoDataFrame(merged, geometry='geometry')
geo_df.set_crs(epsg=4326, inplace=True)  

geo_df[geo_df['duration'] =='단기'].to_file('st.gpkg')
geo_df[geo_df['duration'] =='중기'].to_file('mt.gpkg')
geo_df[geo_df['duration'] =='장기'].to_file('lt.gpkg') 


In [ ]:
import matplotlib.pyplot as plt
import matplotlib as mpl
# 한글폰트 사용, 음수표시, 굵은글씨 적용
mpl.rcParams['axes.unicode_minus'] = False
mpl.rcParams['font.family'] = 'Malgun Gothic'
mpl.rcParams['font.weight'] = 'bold'

#시-도 경계선 파일을 불러와 위경도 좌표계로 변환(위경도가 플롯이 예쁨)
gdf = gpd.read_file('ctprvn.gpkg') #'ctprvn.gpkg'
gdf = gdf.to_crs(epsg=4326)

# 이미지 저장할 경로 만들기
if not os.path.isdir('./PLOT'):
    os.makedirs('./PLOT')

# 데이터를 선택
for datacol in ['SU', 'ID', 'FD', 'TR', 'CDD', 'CWD', 'TXX',
       'TXN', 'TNX', 'TNN', 'TX90p', 'TX10p', 'TN90p', 'TN10p', 'R10', 'R20', 'R72',
       'R100', 'RX1day', 'RX5day', 'R95P', 'R99P', 'PRCPTOT', 'SDII', 'DTR']:
    # 기간 범주를 선택
    for lookup in ['단기', '중기', '장기']:
        
        # 플롯과 지도그리기
        plt.figure(figsize=(10,10))
        gdf.plot(ax=plt.gca(), color='lightgrey', edgecolor='grey')    
        
        # 선택된 데이터를 양수,음수,0로 나누어 scatter plot수행
        geo_df2 = geo_df[geo_df['duration'] == lookup]

        # 각 데이터 별 최대 최소값 구하기
        max_val = max(geo_df2[datacol])
        min_val = min(geo_df2[datacol])

        # 3등분 할 기준 값
        max_bal = max_val / 3
        min_bal = min_val / 3

        # 0 이상 값 들 3등분
        pos_1 = geo_df2[geo_df2[datacol].between(0, max_bal)]
        pos_2 = geo_df2[geo_df2[datacol].between(max_bal, max_bal*2)]
        pos_3 = geo_df2[geo_df2[datacol].between(max_bal*2, max_val)]
        
        # 0 이하 값 들 3등분
        neg_1 = geo_df2[geo_df2[datacol].between(min_bal,0)]
        neg_2 = geo_df2[geo_df2[datacol].between(min_bal*2,min_bal)]
        neg_3 = geo_df2[geo_df2[datacol].between(min_val,min_bal*2)]

        # 0 인경우
        zero = geo_df2[geo_df2[datacol] == 0]
        
        # 크기 20 14 8
        plt.scatter(pos_1['경도'], pos_1['위도'], color='red', marker='^',s=40)
        plt.scatter(pos_2['경도'], pos_2['위도'], color='red', marker='^',s=70)
        plt.scatter(pos_3['경도'], pos_3['위도'], color='red', marker='^',s=100)
        plt.scatter(neg_1['경도'], neg_1['위도'], color='blue', marker='v',s=40)
        plt.scatter(neg_2['경도'], neg_2['위도'], color='blue', marker='v',s=70)
        plt.scatter(neg_3['경도'], neg_3['위도'], color='blue', marker='v',s=100)
        plt.scatter(zero['경도'], zero['위도'], color='white', marker='o',s=100,edgecolor='grey')    
        
        # 지도에 데이터값을 표시
        for idx, row in geo_df2.iterrows():
            plt.text(row['경도']+0.05, row['위도']+0.1, row['station'], fontsize=10, color='black')
            plt.text(row['경도']+0.05, row['위도']+0.001, np.round(row[datacol],4), fontsize=10, color='black')
        plt.title(lookup + ' ' + datacol,fontdict={'fontsize':20})
        
        # x범위를 울릉도까지로 제한(독도까지 다 나오면 너무 멀어져서)
        plt.xlim(124,131.3)
        
        # 그래프 저장후 닫기
        plt.savefig(f'PLOT/{lookup}_{datacol}.png')
        plt.close()
    print(f"{datacol} 끝")
